In [1]:
# Clear workspace
%reset

# standard packages
from math import e
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import pickle as pkl
import os
from sklearn import preprocessing
from sklearn.model_selection import train_test_split, StratifiedKFold
from sklearn.metrics import classification_report, roc_curve, auc, roc_auc_score, precision_recall_curve, plot_precision_recall_curve
from scipy.stats import sem
pd.options.display.max_colwidth = 100

# SGL packages
from group_lasso import LogisticGroupLasso
LogisticGroupLasso.LOG_LOSSES = True

%reload_ext autoreload
%autoreload 2

working_dir = "~/Desktop/hif2gene"


Once deleted, variables cannot be recovered. Proceed (y/[n])? y


In [2]:
seed = 360
np.random.seed(seed)
outcome = 'TIGIT'

## Load in HIFs + Clusters 

In [4]:
# Load in HIF dataset with labels
# NAs removed, already converted to patient-level
df = pd.read_csv("{0}/data/genetic_data/TIGIT/datasets/pancancer.TIGIT.joined.USE.csv".format(working_dir))
df = df.iloc[:,1:]
df

AREA..MM2..OF..EPITHELIAL..IN..TISSUE._HE  \
0                                     71.806464   
1                                     82.396624   
2                                     26.877520   
3                                     43.128576   
4                                      0.685216   
...                                         ...   
1878                                 199.295932   
1879                                  56.896288   
1880                                 146.597648   
1881                                 366.084516   
1882                                 325.681596   

      AREA..MM2..OF..ESI_0080..IN..TISSUE._HE  \
0                                  129.127076   
1                                  168.316672   
2                                   53.040932   
3                                  111.292004   
4                                    2.596956   
...                                       ...   
1878                               105.349612   
1879                                44.219920   
1880                                37.981336   
1881                                29.663968   
1882                               287.985948   

      AREA..MM2..OF..NECROSIS..IN..TISSUE._HE  \
0                                    1.158576   
1                                    2.677280   
2                                    3.571664   
3                                    0.742096   
4                                    1.605504   
...                                       ...   
1878                                 3.874452   
1879                                 3.791788   
1880                                10.317812   
1881                                 8.606332   
1882                                62.556528   

      AREA..MM2..OF..STROMA..IN..TISSUE._HE  \
0                                122.432688   
1                                145.747888   
2                                 44.355952   
3                                 98.095856   
4                                  8.142384   
...                                     ...   
1878                              56.462540   
1879                              22.847336   
1880                              18.585056   
1881                               9.045324   
1882                             143.874736   

      AREA..MM2..OF..TUMOR..IN..TISSUE._HE  \
0                               194.239152   
1                               228.144512   
2                                71.233472   
3                               141.224432   
4                                 8.827600   
...                                    ...   
1878                            255.758472   
1879                             79.743624   
1880                            165.182704   
1881                            375.129840   
1882                            469.556332   

      AREA.PROP...EPITHELIAL..OVER..TUMOR...IN..TISSUE._HE  \
0                                                 0.369681   
1                                                 0.361160   
2                                                 0.377316   
3                                                 0.305390   
4                                                 0.077622   
...                                                    ...   
1878                                              0.779235   
1879                                              0.713490   
1880                                              0.887488   
1881                                              0.975887   
1882                                              0.693594   

      AREA.PROP...ESI_0080..OVER..TUMOR...IN..TISSUE._HE  \
0                                               0.664784   
1                                               0.737763   
2                                               0.744607   
3                                               0.788051   
4                                               0.29

In [5]:
# Normalize HIFs and define X, y
X = df.iloc[:,:607]
X_normalized = (X-X.mean())/X.std()
X_normalized

AREA..MM2..OF..EPITHELIAL..IN..TISSUE._HE  \
0                                      0.361330   
1                                      0.571818   
2                                     -0.531671   
3                                     -0.208668   
4                                     -1.052265   
...                                         ...   
1878                                   2.895290   
1879                                   0.064977   
1880                                   1.847867   
1881                                   6.210354   
1882                                   5.407312   

      AREA..MM2..OF..ESI_0080..IN..TISSUE._HE  \
0                                    1.277181   
1                                    2.037783   
2                                   -0.199519   
3                                    0.931033   
4                                   -1.178549   
...                                       ...   
1878                                 0.815702   
1879                                -0.370720   
1880                                -0.491800   
1881                                -0.653225   
1882                                 4.360357   

      AREA..MM2..OF..NECROSIS..IN..TISSUE._HE  \
0                                   -0.471264   
1                                   -0.395798   
2                                   -0.351355   
3                                   -0.491960   
4                                   -0.449056   
...                                       ...   
1878                                -0.336309   
1879                                -0.340417   
1880                                -0.016131   
1881                                -0.101176   
1882                                 2.579676   

      AREA..MM2..OF..STROMA..IN..TISSUE._HE  \
0                                  1.738874   
1                                  2.297845   
2                                 -0.132980   
3                                  1.155410   
4                                 -1.001184   
...                                     ...   
1878                               0.157270   
1879                              -0.648640   
1880                              -0.750826   
1881                              -0.979537   
1882                               2.252937   

      AREA..MM2..OF..TUMOR..IN..TISSUE._HE  \
0                                 1.168419   
1                                 1.605151   
2                                -0.416006   
3                                 0.485541   
4                                -1.219851   
...                                    ...   
1878                              1.960844   
1879                             -0.306388   
1880                              0.794145   
1881                              3.498455   
1882                              4.714755   

      AREA.PROP...EPITHELIAL..OVER..TUMOR...IN..TISSUE._HE  \
0                                                -0.680931   
1                                                -0.725252   
2                                                -0.641218   
3                                                -1.015329   
4                                                -2.200033   
...                                                    ...   
1878                                              1.449307   
1879                                              1.107345   
1880                                              2.012370   
1881                                              2.472168   
1882                                              1.003860   

      AREA.PROP...ESI_0080..OVER..TUMOR...IN..TISSUE._HE  \
0                                               0.322342   
1                                               0.724480   
2                                               0.762189   
3                                               1.001577   
4                                              -1.71

In [6]:
y = df.iloc[:,607]
print(np.sum(y))

943


In [7]:
# Load in clusters
clusters = pd.read_csv("{0}/data/hif_clusters/pancancer.hif.clusters.csv".format(working_dir))
print("Number of Clusters: {0}".format(len(set(clusters['x']))))
clusters


Number of Clusters: 20


Unnamed: 0  x
0    AREA (MM2) OF [EPITHELIAL] IN [TISSUE]_HE  1
1      AREA (MM2) OF [ESI_0080] IN [TISSUE]_HE  1
2      AREA (MM2) OF [NECROSIS] IN [TISSUE]_HE  2
3        AREA (MM2) OF [STROMA] IN [TISSUE]_HE  3
4         AREA (MM2) OF [TUMOR] IN [TISSUE]_HE  1
..                                         ... ..
602     TOTAL [MACROPHAGE CELLS] IN [TUMOR]_HE  1
603    TOTAL [PLASMA CELLS] IN [EPITHELIAL]_HE  1
604      TOTAL [PLASMA CELLS] IN [ESI_0080]_HE  9
605        TOTAL [PLASMA CELLS] IN [STROMA]_HE  9
606         TOTAL [PLASMA CELLS] IN [TUMOR]_HE  9

[607 rows x 2 columns]

## Define Training Process as Function

In [8]:
def train_process(X_normalized, y):
    # define nested CV parameters
    num_outer_loops = 3 # for estimating generalization error
    num_inner_loops = 5 # for hyper-parameter tuning

    # Define outer loops (A, B, and C)
    X_train_AB, X_train_C, y_train_AB, y_train_C = train_test_split(X_normalized, y, test_size=1/3, random_state=seed, stratify=y)
    X_train_A, X_train_B, y_train_A, y_train_B = train_test_split(X_train_AB, y_train_AB, test_size=1/2, random_state=seed, stratify=y_train_AB)
    
    ################
    # Outer loop 1 #
    ################
    # Define outer loop train and test
    X_train_1 = np.array(X_train_A.append(X_train_B))
    y_train_1 = np.array(y_train_A.append(y_train_B))
    # print(X_train_1.shape, y_train_1.shape)
    
    # No need for cross-validation for hyper-parameter tuning
    # Use already defined hyper-parameters
    optimal_log_reg = -3.6
    optimal_reg = np.exp(optimal_log_reg)
    # print(optimal_log_reg, optimal_reg)

    # Fit "optimal model"
    optimal_sgl = LogisticGroupLasso(groups=clusters['x'], group_reg=optimal_reg*(1/6), l1_reg=optimal_reg*(5/6), n_iter=1000, 
                             tol=1e-6, old_regularisation=False, warm_start=False, random_state=seed)
    optimal_sgl.fit(X_train_1, y_train_1)

    # Store optimal model
    optimal_sgl_1 = optimal_sgl
    
    # Store betas
    sparsity_mask = optimal_sgl.sparsity_mask_
    betas_1 = optimal_sgl.coef_[:, 1] - optimal_sgl.coef_[:, 0]
    betas_1[~sparsity_mask] = 0.0 # if not included in model, set to 0
    
    ################
    # Outer loop 2 #
    ################
    # Define outer loop train and test
    X_train_2 = np.array(X_train_A.append(X_train_C))
    y_train_2 = np.array(y_train_A.append(y_train_C))
    
    # Use already defined hyper-parameters
    optimal_log_reg = -3.6
    optimal_reg = np.exp(optimal_log_reg)
    # print(optimal_log_reg, optimal_reg)

    # Fit "optimal model"
    optimal_sgl = LogisticGroupLasso(groups=clusters['x'], group_reg=optimal_reg*(1/6), l1_reg=optimal_reg*(5/6), n_iter=1000, 
                             tol=1e-6, old_regularisation=False, warm_start=False, random_state=seed)
    optimal_sgl.fit(X_train_2, y_train_2)

    # Store optimal model
    optimal_sgl_2 = optimal_sgl
    
    # Store betas
    sparsity_mask = optimal_sgl.sparsity_mask_
    betas_2 = optimal_sgl.coef_[:, 1] - optimal_sgl.coef_[:, 0]
    betas_2[~sparsity_mask] = 0.0 # if not included in model, set to 0
    
    ################
    # Outer loop 3 #
    ################
    # Define outer loop train and test
    X_train_3 = np.array(X_train_B.append(X_train_C))
    y_train_3 = np.array(y_train_B.append(y_train_C))
    
    # Choose best regularization parameter based on CV plot
    optimal_log_reg = -3.6
    optimal_reg = np.exp(optimal_log_reg)
    # print(optimal_log_reg, optimal_reg)

    # Fit "optimal model"
    optimal_sgl = LogisticGroupLasso(groups=clusters['x'], group_reg=optimal_reg*(1/6), l1_reg=optimal_reg*(5/6), n_iter=1000, 
                             tol=1e-6, old_regularisation=False, warm_start=False, random_state=seed)
    optimal_sgl.fit(X_train_3, y_train_3)

    # Store optimal model
    optimal_sgl_3 = optimal_sgl
    
    # Store betas
    sparsity_mask = optimal_sgl.sparsity_mask_
    betas_3 = optimal_sgl.coef_[:, 1] - optimal_sgl.coef_[:, 0]
    betas_3[~sparsity_mask] = 0.0 # if not included in model, set to 0
    
    ##################
    # Ensemble betas #
    ##################
    betas_df = pd.DataFrame({
        "HIF": clusters['Unnamed: 0'],
        "Beta_1": betas_1, 
        "Beta_2": betas_2,
        "Beta_3": betas_3,
        "Cluster": clusters['x']
        }
    )
    betas_df['Beta'] = (betas_df['Beta_1'] + betas_df['Beta_2'] + betas_df['Beta_3'])/3.0
    
    return betas_df[['HIF', 'Beta']]
    

## Run Permutation Test

In [8]:
num_iterations = 5000 # 1000
hif_null_distributions = {}

for hif_name in clusters['Unnamed: 0']:
    hif_null_distributions[hif_name] = []

In [9]:
# Generate N permutations of binary y vector
# Permutation = Sample WITHOUT replacement
y_permutations = []
for i in range(num_iterations):
    y_permutations.append(np.random.choice(y, size=(len(y), ), replace=False))
# y_permutations

In [10]:
# sanity check
print(np.sum(y), np.sum(y_permutations[0]), np.sum(y_permutations[1]))

943 943 943


In [ ]:
for iteration in range(num_iterations):
    y_perm = pd.DataFrame(y_permutations[iteration])
    
    # Same X, permuted Y
    betas_df = train_process(X_normalized, y_perm)
    
    # Add to null distribution samples
    for index, row in betas_df.iterrows():
        hif_null_distributions[row['HIF']].append(row['Beta'])

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it 

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

...

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

In [ ]:
betas_df.sort_values(by='Beta', ascending=False)

In [ ]:
for k, v in hif_null_distributions.items():
    print(k)
    print(sorted(v))
    break